In [1]:
import os

# Load configuration from YAML file
config = {
    "model_name": "llama3-70b-8192",
}


In [2]:
import json
import yaml
from langchain.prompts import ChatPromptTemplate
from langchain.chat_models import ChatOpenAI
from langchain.schema.output_parser import StrOutputParser

class TaskDescriptionGenerator:
    def __init__(self, model_temperature=0.7):
        self.model = ChatOpenAI(model=config["model_name"], temperature=model_temperature)
        self.output_parser = StrOutputParser()
        
        self.description_prompt = ChatPromptTemplate.from_template(
            """Given the following JSON example for a task type:
            {raw_example}

            Provide a concise description of the task type, including the format and style of the output.

            Format your response as follows:
            Task Description: [Your description here]
            """
        )

        self.briefs_prompt = ChatPromptTemplate.from_template(
            """Given the following task type description:
            Task Description: {description}

            Generate descriptions for 3 new examples with detailed attributes
            based on this task type.

            Format your response as a valid YAML object with a single key
            'brief_descriptions' containing a YAML array of 3 objects, each
            with a 'description' field.
            """
        )

        self.examples_from_briefs_prompt = ChatPromptTemplate.from_template(
            """Given the following task type description, brief description for new examples, 
            and JSON example:

            Task Description: {description}
            Brief Description: {brief_description}

            Example:
            {raw_example}

            Generate 3 more input/output examples for this task type, based on the brief
            description, in the same JSON format.

            Format your response as a valid JSON object with a single key 'examples' 
            containing a JSON array of 3 objects, each with 'input' and 'output' fields.
            """
        )

        self.examples_prompt = ChatPromptTemplate.from_template(
            """Given the following task type description, and input/output example:
            Task Description: {description}
            Example: {example}

            Generate 3 new input/output examples for this task type.

            Format your response as a valid JSON object with a single key 'examples' 
            containing a JSON array of 3 objects, each with 'input' and 'output' fields.
            """
        )

        self.description_chain = self.description_prompt | self.model | self.output_parser
        self.briefs_chain = self.briefs_prompt | self.model | self.output_parser
        # bind json_object to the model
        json_model = self.model.bind(response_format={"type": "json_object"})
        self.examples_from_briefs_chain = self.examples_from_briefs_prompt | json_model | self.output_parser
        self.examples_chain = self.examples_prompt | json_model | self.output_parser

    def generate_description(self, raw_example_str):
        result = self.description_chain.invoke({
            "raw_example": raw_example_str
        })
        return result.split("Task Description: ")[1].strip()

    def generate_briefs(self, description):
        result = self.briefs_chain.invoke({
            "description": description
        })
        # return result.split("Brief Description: ")[1].strip()
        return result

    def generate_examples_from_briefs(self, description, brief_description, raw_example_str):
        result = self.examples_from_briefs_chain.invoke({
            "description": description,
            "brief_description": brief_description,
            "raw_example": raw_example_str
        })

        try:
            result = result.strip()
            if result.startswith('```') and result.endswith('```'):
                result = result.strip('```').strip()
                if result.startswith('json'):
                    result = result.strip('json').strip()
            return json.loads(result)
        except json.JSONDecodeError as e:
            raise ValueError(f"The generated examples are not in valid JSON format. Error: {str(e)} Result: {result}")
        
    def generate_examples(self, description, example):
        result = self.examples_chain.invoke({
            "description": description,
            "example": example
        })
        
        try:
            result = result.strip()
            if result.startswith('```') and result.endswith('```'):
                result = result.strip('```').strip()
                if result.startswith('json'):
                    result = result.strip('json').strip()
            return json.loads(result)
        except json.JSONDecodeError as e:
            raise ValueError(f"The generated examples are not in valid JSON format. Error: {str(e)} Result: {result}")

    def process(self, input_str):
        try:
            # Try to parse as JSON
            try:
                data = json.loads(input_str)
            except json.JSONDecodeError:
                # If JSON parsing fails, try to parse as YAML
                try:
                    data = yaml.safe_load(input_str)
                except yaml.YAMLError as e:
                    raise ValueError("Invalid input string. Error: {}".format(str(e)))
            
            if not isinstance(data, dict) or 'input' not in data or 'output' not in data:
                raise ValueError("Invalid input format. Expected an object with 'input' and 'output' fields.")
            
            description = self.generate_description(json.dumps(data, ensure_ascii=False))
            brief_description = self.generate_briefs(description)
            new_examples_from_briefs = self.generate_examples_from_briefs(description, brief_description, json.dumps(data, ensure_ascii=False))
            new_examples = self.generate_examples(description, json.dumps(data, ensure_ascii=False))
    
            output = {
                "task_description": description,
                "brief_description": brief_description,
                "additional_examples": list(new_examples_from_briefs.values()) + list(new_examples.values())
            }
            
            return json.dumps(output, indent=2, ensure_ascii=False)
        
        except Exception as e:
            raise RuntimeError(f"An error occurred during processing: {str(e)}")
    

import gradio as gr

def process_json(input_json):
    try:
        generator = TaskDescriptionGenerator()
        result = generator.process(input_json)
        return "Process completed successfully. Result:\n" + result
    except Exception as e:
        return f"An error occurred: {str(e)}"

demo = gr.Interface(
    fn=process_json,
    inputs=gr.Textbox(label="Input JSON"),
    outputs=gr.Textbox(label="Output"),
    title="Task Description Generator",
    description="Enter a JSON object with 'input' and 'output' fields to generate a task description and additional examples."
)

if __name__ == "__main__":
    demo.launch()

/home/yale/work/meta-prompt/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.


/home/yale/work/meta-prompt/.venv/lib/python3.10/site-packages/langchain_core/_api/deprecation.py:141: LangChainDeprecationWarning: The class `ChatOpenAI` was deprecated in LangChain 0.0.10 and will be removed in 0.3.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import ChatOpenAI`.
  warn_deprecated(
